In [2]:
import pandas as pd
import numpy as np
import pandas_profiling as pp
from sklearn.linear_model import LogisticRegression, Ridge, Lasso
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier, BaggingClassifier
from sklearn.model_selection import StratifiedKFold, KFold, GridSearchCV, RandomizedSearchCV
from sklearn.metrics import roc_auc_score, make_scorer
from sklearn.svm import SVC

In [3]:
train = pd.read_csv(r'E:\PycharmProjects\Machine_L\Data_Science_Club\fivth\train.csv', delimiter = '\t')
#train.drop(['Unnamed: 0'], inplace = True)
train = train.loc[:, '0':]
test = pd.read_csv(r'E:\PycharmProjects\Machine_L\Data_Science_Club\fivth\test.csv', delimiter = '\t')
test = test.loc[:, '0':]
train.head()

0  1  2  3  4  5  6         7  8  9 ...        336  337  338  339  340  \
0  1  1  0  0  0  0  0  0.090909  0  0 ...   0.221395    0    1    0    0   
1  1  1  0  0  1  0  0  0.090909  0  0 ...   0.241508    0    1    0    0   
2  0  1  0  0  1  0  0  0.090909  0  0 ...   0.123067    0    1    0    0   
3  0  1  0  0  1  0  0  0.136364  0  0 ...   0.296065    0    0    1    0   
4  0  1  0  0  1  0  0  0.136364  0  0 ...   0.178956    0    0    1    0   

        341  342  343  344  345  
0  0.222222    1    1    1    1  
1  0.111111    1    1    1    0  
2  0.444444    1    1    1    1  
3  0.222222    1    1    1    0  
4  0.111111    1    1    1    1  

[5 rows x 346 columns]

In [3]:
pp.ProfileReport(train)

In [4]:
pp.ProfileReport(test)

In [4]:
X = train.loc[:, '1':]
y = train['0']

In [24]:
#baseline LinearRegression
grid = {'C': [0.0001, 0.001, 0.01, 0.1, 1, 10, 100, 1000]}
kf = StratifiedKFold(n_splits = 5, shuffle = True, random_state = 42)
score = make_scorer(roc_auc_score)
gs_b_log = GridSearchCV(LogisticRegression(random_state = 42), scoring = 'roc_auc', param_grid = grid, cv = kf, verbose = 2)
gs_b_log.fit(X, y)

Fitting 5 folds for each of 8 candidates, totalling 40 fits
[CV] C=0.0001 ........................................................
[CV] ......................................... C=0.0001, total=   0.3s
[CV] C=0.0001 ........................................................


[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.3s remaining:    0.0s


[CV] ......................................... C=0.0001, total=   0.2s
[CV] C=0.0001 ........................................................
[CV] ......................................... C=0.0001, total=   0.2s
[CV] C=0.0001 ........................................................
[CV] ......................................... C=0.0001, total=   0.2s
[CV] C=0.0001 ........................................................
[CV] ......................................... C=0.0001, total=   0.2s
[CV] C=0.001 .........................................................
[CV] .......................................... C=0.001, total=   0.4s
[CV] C=0.001 .........................................................
[CV] .......................................... C=0.001, total=   0.4s
[CV] C=0.001 .........................................................
[CV] .......................................... C=0.001, total=   0.4s
[CV] C=0.001 .........................................................
[CV] .

[Parallel(n_jobs=1)]: Done  40 out of  40 | elapsed:  3.0min finished


GridSearchCV(cv=StratifiedKFold(n_splits=5, random_state=42, shuffle=True),
       error_score='raise',
       estimator=LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='ovr', n_jobs=1,
          penalty='l2', random_state=42, solver='liblinear', tol=0.0001,
          verbose=0, warm_start=False),
       fit_params=None, iid=True, n_jobs=1,
       param_grid={'C': [0.0001, 0.001, 0.01, 0.1, 1, 10, 100, 1000]},
       pre_dispatch='2*n_jobs', refit=True, return_train_score='warn',
       scoring='roc_auc', verbose=2)

In [25]:
gs.best_score_

0.7276539121936928

In [5]:
#dropping features that is constant in both train and test
train.drop(['140', '164'], axis = 1, inplace = True)
test.drop(['140', '164'], inplace = True, axis = 1)

In [6]:
corelations = [] # list of corelation coefs between target and each feature
for i in range(1, len(train.columns.tolist())):
    if (i == 140 or i == 164):
        continue
    corelations.append(train.loc[:, '0'].corr(train.loc[:, str(i)]))

In [7]:
print('Min {}\nMax {}'.format(min(np.fabs(corelations)), max(np.fabs(corelations))))

Min 3.6283651172678677e-06
Max 0.1555224788292514


In [8]:
indexes = [i for i in range(len(corelations)) if np.fabs(corelations[i]) < 1e-4] # target doesn't depend on these features so much

In [9]:
indexes

[222, 264, 273]

In [11]:
#x = train.drop(['2', '9', '17'], axis = 1).loc[:, '1':]
x = train.drop(['222', '264', '273'], axis = 1).loc[:, '1':]# drop features with small cor with target

In [12]:
# LogisticRegression with feature preprocessing (best yet - gives 0.7358 on lb)
grid = {'C': [0.0001, 0.001, 0.01, 0.1, 1, 10, 100, 1000]}
kf = StratifiedKFold(n_splits = 5, shuffle = True, random_state = 42)
score = make_scorer(roc_auc_score)
gs = GridSearchCV(LogisticRegression(random_state = 42), scoring = 'roc_auc', param_grid = grid, cv = kf, verbose = 2)
gs.fit(x, y)

Fitting 5 folds for each of 8 candidates, totalling 40 fits
[CV] C=0.0001 ........................................................
[CV] ......................................... C=0.0001, total=   0.3s
[CV] C=0.0001 ........................................................


[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.4s remaining:    0.0s


[CV] ......................................... C=0.0001, total=   0.3s
[CV] C=0.0001 ........................................................
[CV] ......................................... C=0.0001, total=   0.2s
[CV] C=0.0001 ........................................................
[CV] ......................................... C=0.0001, total=   0.3s
[CV] C=0.0001 ........................................................
[CV] ......................................... C=0.0001, total=   0.3s
[CV] C=0.001 .........................................................
[CV] .......................................... C=0.001, total=   0.4s
[CV] C=0.001 .........................................................
[CV] .......................................... C=0.001, total=   0.4s
[CV] C=0.001 .........................................................
[CV] .......................................... C=0.001, total=   0.4s
[CV] C=0.001 .........................................................
[CV] .

[Parallel(n_jobs=1)]: Done  40 out of  40 | elapsed:  3.1min finished


GridSearchCV(cv=StratifiedKFold(n_splits=5, random_state=42, shuffle=True),
       error_score='raise',
       estimator=LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='ovr', n_jobs=1,
          penalty='l2', random_state=42, solver='liblinear', tol=0.0001,
          verbose=0, warm_start=False),
       fit_params=None, iid=True, n_jobs=1,
       param_grid={'C': [0.0001, 0.001, 0.01, 0.1, 1, 10, 100, 1000]},
       pre_dispatch='2*n_jobs', refit=True, return_train_score='warn',
       scoring='roc_auc', verbose=2)

In [13]:
gs.best_score_# best log regression yet (dropping 140 164 222 264 273) cross_val_score on best log

0.7276539121936928

In [14]:
X_test = test.drop(['222', '264', '273'], axis = 1).loc[:, '1':]

In [26]:
X = train.loc[:, '1':]

In [27]:
grid = {'C': [0.0001, 0.001, 0.01, 0.1, 1, 10, 100, 1000]}
kf = StratifiedKFold(n_splits = 5, shuffle = True, random_state = 42)
score = make_scorer(roc_auc_score)
gs2 = GridSearchCV(LogisticRegression(random_state = 42), scoring = 'roc_auc', param_grid = grid, cv = kf, verbose = 2)
gs2.fit(X, y)

Fitting 5 folds for each of 8 candidates, totalling 40 fits
[CV] C=0.0001 ........................................................
[CV] ......................................... C=0.0001, total=   0.3s
[CV] C=0.0001 ........................................................


[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.3s remaining:    0.0s


[CV] ......................................... C=0.0001, total=   0.3s
[CV] C=0.0001 ........................................................
[CV] ......................................... C=0.0001, total=   0.3s
[CV] C=0.0001 ........................................................
[CV] ......................................... C=0.0001, total=   0.3s
[CV] C=0.0001 ........................................................
[CV] ......................................... C=0.0001, total=   0.3s
[CV] C=0.001 .........................................................
[CV] .......................................... C=0.001, total=   0.4s
[CV] C=0.001 .........................................................
[CV] .......................................... C=0.001, total=   0.4s
[CV] C=0.001 .........................................................
[CV] .......................................... C=0.001, total=   0.4s
[CV] C=0.001 .........................................................
[CV] .

[Parallel(n_jobs=1)]: Done  40 out of  40 | elapsed:  3.0min finished


GridSearchCV(cv=StratifiedKFold(n_splits=5, random_state=42, shuffle=True),
       error_score='raise',
       estimator=LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='ovr', n_jobs=1,
          penalty='l2', random_state=42, solver='liblinear', tol=0.0001,
          verbose=0, warm_start=False),
       fit_params=None, iid=True, n_jobs=1,
       param_grid={'C': [0.0001, 0.001, 0.01, 0.1, 1, 10, 100, 1000]},
       pre_dispatch='2*n_jobs', refit=True, return_train_score='warn',
       scoring='roc_auc', verbose=2)

In [28]:
gs2.best_score_

0.7276102429049652

In [17]:
'''
gs.best_estimator_.fit(x,train['0'])
result = pd.DataFrame(gs.best_estimator_.predict_proba(X_test))
pred=pd.Series(result.iloc[:,1])
pred.to_csv('submission3.csv',header = True, index_label = True) # subm 3 - best for log reg yet (0.73582711)
'''

"\ngs.best_estimator_.fit(X,train['0'])\nresult = pd.DataFrame(gs.best_estimator_.predict_proba(X_test))\npred=pd.Series(result.iloc[:,1])\npred.to_csv('submission3.csv',header = True, index_label = True) # subm 3 - best for log reg yet (0.73582711)\n"

In [19]:
# RandomForest baseline 
parameters = {'max_features': [4, 7, 10, 13], 'min_samples_leaf': [1, 3, 5, 7], 'max_depth': [5,10,15,20]}
rfc = RandomForestClassifier(n_estimators=100, random_state=42, n_jobs=-1)
gcv = GridSearchCV(rfc, parameters, n_jobs=-1, cv=kf, verbose=1, scoring = 'roc_auc')
gcv.fit(X, y)

Fitting 5 folds for each of 64 candidates, totalling 320 fits


[Parallel(n_jobs=-1)]: Done  34 tasks      | elapsed:   16.6s
[Parallel(n_jobs=-1)]: Done 184 tasks      | elapsed:  1.9min
[Parallel(n_jobs=-1)]: Done 320 out of 320 | elapsed:  4.5min finished


GridSearchCV(cv=StratifiedKFold(n_splits=5, random_state=42, shuffle=True),
       error_score='raise',
       estimator=RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
            max_depth=None, max_features='auto', max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=1, min_samples_split=2,
            min_weight_fraction_leaf=0.0, n_estimators=100, n_jobs=-1,
            oob_score=False, random_state=42, verbose=0, warm_start=False),
       fit_params=None, iid=True, n_jobs=-1,
       param_grid={'max_features': [4, 7, 10, 13], 'min_samples_leaf': [1, 3, 5, 7], 'max_depth': [5, 10, 15, 20]},
       pre_dispatch='2*n_jobs', refit=True, return_train_score='warn',
       scoring='roc_auc', verbose=1)

In [20]:
gcv.best_score_# cross_val_score 

0.7280618163273905

In [23]:
gcv.best_estimator_.fit(X,train['0'])
result = pd.DataFrame(gcv.best_estimator_.predict_proba(test.loc[:, "1":]))
pred=pd.Series(result.iloc[:,1])
pred.to_csv('submission_base_rand_for.csv',header = True, index_label = True)

In [16]:
# Randomforest with preprocessing (lb - 0.73582711) drop 222 264 273 140 164
X_ = train.drop(['2', '17'], axis = 1)
parameters = {'max_features': [4, 7, 10, 13], 'min_samples_leaf': [1, 3, 5, 7], 'max_depth': [5,10,15,20]}
rfc = RandomForestClassifier(n_estimators=100, random_state=42, n_jobs=-1)
gcv1 = GridSearchCV(rfc, parameters, n_jobs=-1, cv=kf, verbose=1, scoring = 'roc_auc')
gcv1.fit(x, y)

Fitting 5 folds for each of 64 candidates, totalling 320 fits


[Parallel(n_jobs=-1)]: Done  34 tasks      | elapsed:   16.8s
[Parallel(n_jobs=-1)]: Done 184 tasks      | elapsed:  1.9min
[Parallel(n_jobs=-1)]: Done 320 out of 320 | elapsed:  4.5min finished


GridSearchCV(cv=StratifiedKFold(n_splits=5, random_state=42, shuffle=True),
       error_score='raise',
       estimator=RandomForestClassifier(bootstrap=True, class_weight=None, criterion='gini',
            max_depth=None, max_features='auto', max_leaf_nodes=None,
            min_impurity_decrease=0.0, min_impurity_split=None,
            min_samples_leaf=1, min_samples_split=2,
            min_weight_fraction_leaf=0.0, n_estimators=100, n_jobs=-1,
            oob_score=False, random_state=42, verbose=0, warm_start=False),
       fit_params=None, iid=True, n_jobs=-1,
       param_grid={'max_features': [4, 7, 10, 13], 'min_samples_leaf': [1, 3, 5, 7], 'max_depth': [5, 10, 15, 20]},
       pre_dispatch='2*n_jobs', refit=True, return_train_score='warn',
       scoring='roc_auc', verbose=1)

In [17]:
gcv1.best_score_# cross_val_score

0.7286051669957436

In [18]:
gcv1.best_estimator_.fit(x,train['0'])
result = pd.DataFrame(gcv1.best_estimator_.predict_proba(X_test))
pred=pd.Series(result.iloc[:,1])
pred.to_csv('submission_rand_for.csv',header = True, index_label = True)

In [29]:
#stacking and ansamble
log_reg_cl = gs.best_estimator_
forest_cl=gcv1.best_estimator_
а_predictions = []
b_predictions = []
for train, val in kf.split(x, y):
    log_reg_cl.fit(x.iloc[train], y[train])
    forest_cl.fit(x.iloc[train], y[train])
    а_predictions.append([y[val], log_reg_cl.predict_proba(x.iloc[val])[:,1]])
    b_predictions.append([y[val], forest_cl.predict_proba(x.iloc[val])[:,1]])

In [30]:
log_res = log_reg_cl.predict_proba(X_test)
forest_res = forest_cl.predict_proba(X_test)

In [31]:
result = [ (a_p*b_p)**(1/2) for a_p, b_p in zip(log_res, forest_res)]

In [34]:
result = pd.DataFrame(result)
result.columns = ['log_pred', 'forest_pred']
result.head()

log_pred  forest_pred
0  0.844675     0.142912
1  0.569321     0.430258
2  0.829136     0.169047
3  0.671317     0.328646
4  0.531461     0.464647

In [49]:
#ansamble log regression and random forest
final_result = [0 if result.iloc[i,0]>result.iloc[i,1] else 1 for i in result.index]
final_result = pd.Series(final_result)
final_result.head()

0    0
1    0
2    0
3    0
4    0
dtype: int64

In [50]:
final_result.to_csv('submission_ansamble.csv',header = True, index_label = True) #0.74189616

In [68]:
#stacking
x['log'] = 0
x['fr'] = 0
for i, fold in enumerate(kf.split(x, y)):
    train, val = fold[0], fold[1]
    x.iloc[val, -2] = log_res[i][1]
    x.iloc[val, -1] = forest_res[i][1]

In [69]:
x.head()

1  2  3  4  5  6         7  8  9  10    ...     338  339  340       341  \
0  1  0  0  0  0  0  0.090909  0  0   1    ...       1    0    0  0.222222   
1  1  0  0  1  0  0  0.090909  0  0   1    ...       1    0    0  0.111111   
2  1  0  0  1  0  0  0.090909  0  0   1    ...       1    0    0  0.444444   
3  1  0  0  1  0  0  0.136364  0  0   1    ...       0    1    0  0.222222   
4  1  0  0  1  0  0  0.136364  0  0   1    ...       0    1    0  0.111111   

   342  343  344  345       log        fr  
0    1    1    1    1  0.193189  0.147921  
1    1    1    1    0  0.324618  0.332725  
2    1    1    1    1  0.444859  0.416137  
3    1    1    1    0  0.324618  0.332725  
4    1    1    1    1  0.324618  0.332725  

[5 rows x 342 columns]

In [70]:
X_test['log'] = result.loc[:, 'log_pred']
X_test['for'] = result.loc[:, 'forest_pred']

In [71]:
X_test.head()

1  2  3  4  5  6         7  8  9  10    ...     338  339  340       341  \
0  1  0  0  1  0  0  0.136364  0  0   1    ...       1    0    0  0.222222   
1  1  0  0  1  0  0  0.181818  0  0   1    ...       1    0    0  0.000000   
2  1  0  0  0  0  0  0.090909  0  0   1    ...       1    0    0  0.222222   
3  1  0  0  1  0  0  0.090909  0  0   1    ...       1    0    0  0.000000   
4  1  0  0  1  0  0  0.090909  0  0   1    ...       0    1    0  0.000000   

   342  343  344  345       log       for  
0    1    1    1    1  0.844675  0.142912  
1    1    1    1    0  0.569321  0.430258  
2    1    1    1    0  0.829136  0.169047  
3    1    1    1    0  0.671317  0.328646  
4    1    1    1    1  0.531461  0.464647  

[5 rows x 342 columns]

In [72]:
from sklearn.ensemble import ExtraTreesClassifier
r_tree = ExtraTreesClassifier(n_estimators=5, random_state=42, n_jobs=-1)
gs_st = GridSearchCV(estimator=r_tree, param_grid= parameters, n_jobs=-1, cv=kf, verbose=1, scoring = 'roc_auc')
gs_st.fit(x, y)

Fitting 5 folds for each of 64 candidates, totalling 320 fits


[Parallel(n_jobs=-1)]: Done  34 tasks      | elapsed:    9.2s
[Parallel(n_jobs=-1)]: Done 184 tasks      | elapsed:   30.7s
[Parallel(n_jobs=-1)]: Done 320 out of 320 | elapsed:   51.3s finished


GridSearchCV(cv=StratifiedKFold(n_splits=5, random_state=42, shuffle=True),
       error_score='raise',
       estimator=ExtraTreesClassifier(bootstrap=False, class_weight=None, criterion='gini',
           max_depth=None, max_features='auto', max_leaf_nodes=None,
           min_impurity_decrease=0.0, min_impurity_split=None,
           min_samples_leaf=1, min_samples_split=2,
           min_weight_fraction_leaf=0.0, n_estimators=5, n_jobs=-1,
           oob_score=False, random_state=42, verbose=0, warm_start=False),
       fit_params=None, iid=True, n_jobs=-1,
       param_grid={'max_features': [4, 7, 10, 13], 'min_samples_leaf': [1, 3, 5, 7], 'max_depth': [5, 10, 15, 20]},
       pre_dispatch='2*n_jobs', refit=True, return_train_score='warn',
       scoring='roc_auc', verbose=1)

In [73]:
gs_st.best_score_

0.709084793239423

In [75]:
gs_st.best_estimator_.fit(x, y)
result = pd.DataFrame(gs_st.best_estimator_.predict_proba(X_test))
pred=pd.Series(result.iloc[:,1])
pred.to_csv('submission_stack.csv',header = True, index_label = True)

In [28]:
# bagging best log regression model (lb - 0.7358)
parameters = {'max_features': [0.5, 0.7, 0.9, 1.], 'max_samples': [0.5, 0.7, 0.9, 1.], "base_estimator__C": [0.005, 0.001, 0.01]}
bg = BaggingClassifier(gs.best_estimator_, random_state=42, n_estimators=25)
r_grid_search = RandomizedSearchCV(bg, parameters, scoring ='roc_auc', n_iter=10, cv=kf, random_state=1)
r_grid_search = r_grid_search.fit(x, y)
print(r_grid_search.best_score_)# cross_val_score for bagging

0.7119103542865586


In [31]:
r_grid_search.best_estimator_.fit(x,train['0'])
result = pd.DataFrame(r_grid_search.best_estimator_.predict_proba(X_test))
pred=pd.Series(result.iloc[:,1])
pred.to_csv('submission_bagging.csv',header = True, index_label = True)

In [ ]:
#GradientBoosting feature preprocessing
skf = StratifiedKFold(n_splits = 5, shuffle = True, random_state = 42)
parameters = {'max_features': [4, 7, 10, 13], 'min_samples_leaf': [1, 3, 5, 7], 'max_depth': [5,10,15,20]}
grb = GradientBoostingClassifier(n_estimators=100, random_state=42)
gcv_boost = GridSearchCV(grb, parameters, n_jobs=-1, cv=skf, verbose=1, scoring = 'roc_auc')
gcv_boost.fit(x, y)

Fitting 5 folds for each of 64 candidates, totalling 320 fits


[Parallel(n_jobs=-1)]: Done  34 tasks      | elapsed:   25.5s
[Parallel(n_jobs=-1)]: Done 184 tasks      | elapsed:  7.5min
